<a href="https://colab.research.google.com/github/dsercam/NLP/blob/main/MNA_NLP_semana_5_Actividad_Embeddings_abril_2024.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Maestría en Inteligencia Artificial Aplicada**

## Curso: **Procesamiento de Lenguaje Natural**

### Tecnológico de Monterrey

### Prof Luis Eduardo Falcón Morales

## Adtividad Semana 5

### **Vectores Embebidos Pre-entrenados: Fasttext**

#### **Nombres y matrículas de los integrantes del equipo:**



*   Oscar Antonio Suárez Valdez A01323987
*   Dante Rodrigo Serna Camarillo A01182676
*   Elemento de lista



In [65]:
# Aquí deberás incluir todas las librerías que requieras durante esta actividad:
import pandas as pd
from sklearn.model_selection import train_test_split
import numpy as np
import csv

from collections import Counter
import nltk
from nltk.corpus import stopwords
import spacy

import re
import string
import requests

In [66]:
#SE PUEDE USAR EL SIGUIENTE CODIGO PARA RECUPERAR LOS ARCHIVOS DE un REPO PERSONAL EN GITHUB, SIN TENER QUE CARGARLOS MANUALMENTE AL ENTORNO DE COLAB

url = 'https://raw.githubusercontent.com/dsercam/NLP/main/yelp5.txt'
resp = requests.get(url)
with open('yelp5.txt', 'wb') as f:
    f.write(resp.content)
    f.close()

url = 'https://raw.githubusercontent.com/dsercam/NLP/main/imdb5.txt'
resp = requests.get(url)
with open('imdb5.txt', 'wb') as f:
    f.write(resp.content)
    f.close()

url = 'https://raw.githubusercontent.com/dsercam/NLP/main/amazon5.txt'
resp = requests.get(url)
with open('amazon5.txt', 'wb') as f:
    f.write(resp.content)
    f.close()

##**Pregunta - 1:**



Descarga los 3 archivos de Canvas y genera un nuevo DataFrame de Pandas con ellos.

**Llama simplemente "df" a dicho DataFrame.**

Los archivos los encuentras en Canvas: amazon5.txt, imdb5.txt, yelp5.txt.



In [67]:

# ******* Inlcuye a continuación todas las líneas de código y celdas que requieras: ***********

dfa = pd.read_csv('amazon5.txt', sep='\t', names=['review','label'], header=None, encoding='utf-8')
dfi = pd.read_csv('imdb5.txt', delimiter=r"[ ]{2,}", names=['review','label'], header=None, encoding='utf-8', engine='python')
dfy = pd.read_csv('yelp5.txt', sep='\t', names=['review','label'], header=None, encoding='utf-8')

df = pd.concat([dfa, dfi, dfy], ignore_index=True)


# *********** Aquí termina la sección de agregar código *************


In [68]:
# Verifiquemos la información del DataFrame:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3000 entries, 0 to 2999
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   review  3000 non-null   object
 1   label   3000 non-null   int64 
dtypes: int64(1), object(1)
memory usage: 47.0+ KB


In [69]:
# Y veamos sus primeros registros:
df.head()

review  label
0  So there is no way for me to plug it in here i...      0
1                        Good case, Excellent value.      1
2                             Great for the jawbone.      1
3  Tied to charger for conversations lasting more...      0
4                                  The mic is great.      1

##**Pregunta - 2:**

Realiza el proceso de limpieza.

Aplica el preprocesamiento que consideres adecuado, sin embargo, deberás aplicar necesariamente alguna de las técnicas de lematización.











In [70]:
# Stopwords
nltk.download('stopwords')
nltk.download('punkt')
mystopwords = stopwords.words('english')
negwords = [ 'no', 'nor', 'not', 'ain', 'aren', "aren't", 'don', "don't", 'couldn', "couldn't", 'didn', "didn't", 'doesn', "doesn't", 'hadn', "hadn't", 'hasn', "hasn't", 'haven', "haven't", 'isn', "isn't", 'mightn', "mightn't", 'mustn', "mustn't", 'needn', "needn't", 'shan', "shan't", 'shouldn', "shouldn't", 'wasn', "wasn't", 'weren', "weren't", 'won', "won't", 'wouldn', "wouldn't"]
mystopwords = [word for word in mystopwords if word not in negwords]

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [71]:
# Modelo spacy
!python -m spacy download en_core_web_sm
nlp = spacy.load('en_core_web_sm')

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.8/12.8 MB 23.9 MB/s eta 0:00:00
✔ Download and installation successful
You can now load the package via spacy.load('en_core_web_sm')
⚠ Restart to reload dependencies
If you are in a Jupyter or Colab notebook, you may need to restart Python in
order to load all the package's dependencies. You can do this by selecting the
'Restart kernel' or 'Restart runtime' option.


In [73]:
def clean_tok(doc):
  # Minúsculas: Simplificar todo a minúsculas.
  doc = doc.lower()
  # Caracteres alfabéticos: Solo considerar caracteres alfabéticos.
  regexCarAlfabeticos = r'[^a-zA-Z]+'
  doc = re.sub(regexCarAlfabeticos, ' ', doc).strip()
  # Procesa el texto con spacy
  spacy_doc = nlp(doc)
  # Lematizacion
  tokens = [token.lemma_ for token in spacy_doc]
  # Longitud mayor a 1: Se deben considerar solamente tokens de longitud mayor a 1.
  tokens = [token for token in tokens if len(token)>1]
  # Stopwords: Eliminar las stopwords.
  tokens = [token for token in tokens if token not in mystopwords]
  # Simplificar caracteres repetidos más de dos veces
  #tokens = [re.sub(r'(.)\1+', r'\1\1', token) for token in tokens] #good a god, food a fod
  tokens = [re.sub(r'(.)\1{3,}',r'\1\1', token) for token in tokens] #good a good, goood a good

  return tokens

In [76]:

# ******* Inlcuye a continuación todas las líneas de código y celdas que requieras: ***********

 # Separamos la información:
 #     La "X" serán los datos de entrada, los comentarios.
 #     La "Y" será la variable de salida, la evaluación.
 # Ambos, X y Y son "Series"

X = df.review     # Serie de strings
Y = df.label      # Serie de enteros 0s y 1s

assert X.shape == (3000,)           # verificando que tenemos la dimensiones esperadas.
assert Y.shape == (3000,)

# Aplicamos el proceso de limpieza y tokenización:

Xclean = [clean_tok(x) for x in X]



# *********** Aquí termina la sección de agregar código *************

In [77]:
# Despleguemos los primeros comentarios después de tu proceso de limpieza:
for x in Xclean[0:10]:
  print(x)


['no', 'way', 'plug', 'us', 'unless', 'go', 'converter']
['good', 'case', 'excellent', 'value']
['great', 'jawbone']
['tie', 'charger', 'conversation', 'last', 'minute', 'major', 'problem']
['mic', 'great']
['jiggle', 'plug', 'get', 'line', 'right', 'get', 'decent', 'volume']
['several', 'dozen', 'several', 'hundred', 'contact', 'imagine', 'fun', 'send', 'one', 'one']
['razr', 'owner', 'must']
['needless', 'say', 'waste', 'money']
['waste', 'money', 'time']


#**Pregunta - 3:**



Realicemos una partición aleatoria con los mismos porcentajes de la práctica pasada para poder comparar dichos resultados con los de
esta actividad, a saber, 70%, 15% y 15%, para entrenamiento, validación y prueba, respectivamente.

In [78]:

# ************* Inicia la sección de agregar código:*****************************

x_train, x_val_and_test, y_train, y_val_and_test = train_test_split(Xclean, Y, train_size=.70, shuffle=True)
x_val, x_test, y_val, y_test = train_test_split(x_val_and_test, y_val_and_test, test_size=.50, shuffle=True)

print('X,y Train:', len(x_train), len(y_train))      # los "x_" son "list" y los "y_" son "Series"
print('X,y Val:', len(x_val), len(y_val))
print('X,y Test', len(x_test), len(y_test))


# *********** Termina la sección de agregar código *************


# verificemos las dimensiones obtenidas:
print('X,y Train:', len(x_train), len(y_train))
print('X,y Val:', len(x_val), len(y_val))
print('X,y Test', len(x_test), len(y_test))

X,y Train: 2100 2100
X,y Val: 450 450
X,y Test 450 450
X,y Train: 2100 2100
X,y Val: 450 450
X,y Test 450 450


#**Pregunta - 4:**



Construye tu vocabulario a continuación


In [79]:
# a.	Usa el conjunto de entrenamiento para generar tu vocabulario
#     con un tamaño que consideres adecuado:


# ******* Inlcuye a continuación todas las líneas de código y celdas que requieras: ***********

# Diccionario
midiccionario = Counter()
for k in range(len(x_train)):
  midiccionario.update(x_train[k])

# Frecuecia minima
min_freq = 1
midicc = Counter({key: count for key, count in midiccionario.items() if count > min_freq})



# *********** Aquí termina la sección de agregar código *************

In [81]:
# b.	Indica el tamaño del vocabulario generado.

print('Longitud del vocabulario generado:')


# ******* Inicia la sección de agregar código: ***********

print(len(midicc))
print('\n(word,frequency):')
print(midicc.most_common(10))

# *********** Aquí termina la sección de agregar código *************

Longitud del vocabulario generado:
1429

(word,frequency):
[('not', 220), ('good', 214), ('great', 154), ('movie', 149), ('film', 135), ('phone', 120), ('one', 107), ('bad', 106), ('work', 102), ('well', 102)]


c.	¿Por qué debe usarse solamente el conjunto de entrenamiento para generar el vocabulario?


### ++++++++ Inicia la sección de agregar texto: +++++++++++

Se usa solo el conjunto de entrenamiento para evitar el data leakage, asi el modelo no aprende datos que existen en los conjuntos de validacion y entrenamiento. De esta forma se puede evaluar el desempeño del modelo en datos que no ha visto y asi simular como podria desempeñarse en el mundo real.

### ++++++++ Termina la sección de agregar texto: +++++++++++


In [82]:
# d.	Con el vocabulario generado, filtra los conjuntos de entrenamiento,
#     validación y prueba para que todos los comentarios usen solamente las
#     palabras de este vocabulario.

#     Llamar train_x, val_x y test_x a estos tres conjuntos.


# ******* Inlcuye a continuación todas las líneas de código y celdas que requieras: ***********


train_x = []
for k in range(len(x_train)):
  train_x.append([word for word in x_train[k] if word in midicc])

val_x = []
for k in range(len(x_val)):
  val_x.append([word for word in x_val[k] if word in midicc])

test_x = []
for k in range(len(x_test)):
  test_x.append([word for word in x_test[k] if word in midicc])


# *********** Aquí termina la sección de agregar código *************


In [83]:
# Vemos el resultado de los primeros comentarios del conjunto de entrenamiento:

for ss in train_x[0:5]:
  print(ss)

['anyway', 'restaurant', 'wonderful', 'breakfast', 'lunch']
['don', 'go', 'look', 'good', 'food']
['writing', 'fresh', 'bold']
['not', 'say', 'enough', 'good', 'thing', 'place']
['place', 'way', 'mediocre', 'food']


#**Pregunta - 5:**


a. Incluye una tabla comparativa de pros y contras entre los modelos FastText, word2vec de Google y Glove de Stanford.

### ++++++++ Inicia la sección de agregar texto: +++++++++++

None

### ++++++++ Termina la sección de agregar texto: +++++++++++


#**Pregunta - 6:**

Utiliza el modelo FastText de vectores embebidos pre-entrenados de dimensión 300 para generar un nuevo diccionario clave-valor, donde la “clave” será cada token o palabra de tu vocabulario y el “valor” será su vector embebido de dimensión 300.

Este diccionario deberá ser del mismo tamaño que el vocabulario previo que hayas construido previamente.

Es recomendable que una vez que generes el nuevo vocabulario de vectores embebidos, guardes dicho diccionario en un archivo.

Recuerda borrar la variable donde descargaste los 2 millones de vectores embebidos Fasttext.



In [ ]:
!git clone https://github.com/facebookresearch/fastText.git
%cd fastText
!make
!cp fasttext ../
%cd ..

Cloning into 'fastText'...
remote: Enumerating objects: 3998, done.
remote: Counting objects: 100% (1057/1057), done.
remote: Compressing objects: 100% (197/197), done.
remote: Total 3998 (delta 922), reused 889 (delta 855), pack-reused 2941
Receiving objects: 100% (3998/3998), 8.30 MiB | 16.15 MiB/s, done.
Resolving deltas: 100% (2529/2529), done.
/content/fastText
c++ -pthread -std=c++17 -march=native -O3 -funroll-loops -DNDEBUG -c src/args.cc
c++ -pthread -std=c++17 -march=native -O3 -funroll-loops -DNDEBUG -c src/autotune.cc
c++ -pthread -std=c++17 -march=native -O3 -funroll-loops -DNDEBUG -c src/matrix.cc
c++ -pthread -std=c++17 -march=native -O3 -funroll-loops -DNDEBUG -c src/dictionary.cc
c++ -pthread -std=c++17 -march=native -O3 -funroll-loops -DNDEBUG -c src/loss.cc
c++ -pthread -std=c++17 -march=native -O3 -funroll-loops -DNDEBUG -c src/productquantizer.cc
c++ -pthread -std=c++17 -march=native -O3 -funroll-loops -DNDEBUG -c src/densematrix.cc
c++ -pthread -std=c++17 -march=na

In [18]:
!pip install Cython

In [17]:
!pip install fasttext

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 68.8/68.8 kB 2.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Using cached pybind11-2.12.0-py3-none-any.whl (234 kB)
  Created wheel for fasttext: filename=fasttext-0.9.2-cp310-cp310-linux_x86_64.whl size=4227138 sha256=0e05f43baedd77962d39c7b73694087d336c2be420470282c9cdd0acfdd90efd
  Stored in directory: /root/.cache/pip/wheels/a5/13/75/f811c84a8ab36eedbaef977a6a58a98990e8e0f1967f98f394
Successfully built fasttext


In [19]:
import fasttext
import fasttext.util

In [ ]:
# ******* Inlcuye a continuación todas las líneas de código y celdas que requieras: ***********

fasttext.util.download_model('en', if_exists = 'ignore')
ft =fasttext.load_model('cc.en.300.bin')

# *********** Aquí termina la sección de agregar código *************

In [ ]:
vocabEmb = np.zeros((len(midicc), ft.get_dimension()))
vocabEmb.shape

(1435, 300)

In [ ]:
diccEmb = {}

for k,w in enumerate(midicc):
  tmp = ft.get_word_vector(w)
  diccEmb.update({w:tmp})

In [ ]:
diccEmb

{'battery': array([-3.26114893e-02, -2.72182561e-03,  3.19122486e-02,  9.83180329e-02,
         4.42942306e-02, -1.58795975e-02,  9.03700888e-02,  8.09783190e-02,
         2.28916742e-02, -5.51458299e-02,  6.91875592e-02,  3.49675827e-02,
         1.09080128e-01, -7.30025172e-02,  2.57295873e-02,  1.64547246e-02,
        -2.68809404e-02, -1.85313318e-02,  5.71827516e-02, -2.03404501e-02,
         5.77183813e-03, -4.93908450e-02, -4.59107384e-02, -2.61152536e-02,
        -6.37853518e-03,  3.73542309e-02,  3.86190563e-02, -4.90416996e-02,
        -2.63162255e-02,  1.38717115e-01,  9.09792259e-03,  8.41836259e-02,
        -1.89427957e-02, -9.46963765e-03, -1.62956621e-02,  6.11107312e-02,
         2.47086100e-05,  3.28730382e-02,  6.04092842e-03, -6.79397285e-02,
         6.18217140e-02,  4.01560441e-02, -4.84099016e-02, -2.91846301e-02,
        -7.49136508e-02,  6.89020939e-03,  2.30858680e-02, -4.88110036e-02,
        -1.69724058e-02,  3.96607332e-02,  1.00645442e-02,  2.28465488e-03,
 

In [ ]:
outfile = 'diccFastTextEmb.npz'
np.savez(outfile, **diccEmb)

In [ ]:
npzfile = np.load(outfile)
print('npzfile.files: {}'.format(npzfile.files))
print('npzfile["uninteresting"]: {}'.format(npzfile["uninteresting"]))

npzfile.files: ['battery', 'no', 'life', 'result', 'someone', 'soon', 'show', 'make', 'stupid', 'full', 'clich', 'elsewhere', 'love', 'bluetooth', 'waitress', 'friendly', 'happy', 'option', 'not', 'loud', 'enough', 'doesn', 'turn', 'like', 'lot', 'beautiful', 'place', 'fit', 'strong', 'item', 'work', 'great', 'break', 'month', 'use', 'definitely', 'cult', 'classic', 'well', 'worth', 'view', 'share', 'inexpensive', 'piece', 'would', 'still', 'expect', 'quality', 'phone', 'chicken', 'pho', 'taste', 'bland', 'good', 'way', 'describe', 'barely', 'meat', 'unbelievable', 'bargain', 'feature', 'array', 'memorable', 'nut', 'bartender', 'absolutely', 'amazing', 'price', 'european', 'movie', 'nice', 'time', 'student', 'experience', 'live', 'although', 'circumstance', 'different', 'dumb', 'pointless', 'complete', 'waste', 'service', 'fine', 'complaint', 'superb', 'earpiece', 'server', 'attentive', 'serve', 'staff', 'food', 'watch', 'film', 'want', 'learn', 'don', 'miss', 'real', 'sushi', 'lover',

In [ ]:
del ft

In [84]:
url = 'https://github.com/dsercam/NLP/raw/main/diccFastTextEmb.npz'
resp = requests.get(url)
with open('diccFastTextEmb.npz', 'wb') as f:
    f.write(resp.content)
    f.close()


In [85]:
myDiccNPZ = np.load('diccFastTextEmb.npz')

#**Pregunta - 7:**



Generamos los vectores embebidos a paertir de los conjuntos de entrenamiento, validación y preuba.

Los llamaremos trainEmb, valEmb y testEmb, respectivamente.

In [86]:
lst = myDiccNPZ.files
diccEmb = {}

for item in lst:
  diccEmb.update({item:myDiccNPZ[item]})


In [94]:
def featureEmbedding(sentences, embeddingsDictionary):
    DIMENSION = 300 #puede ajustarse si se usan enbeddings con disitnta dimensionalindad
    zero_vector = np.zeros(DIMENSION)
    embeddedSentences = []
    for tokens in sentences:                # para cada review dentro de nuestra lista
        sentenceEmbedding =  np.zeros(DIMENSION)    # np array con longitud del tama;o de nuestra dimension
        #count_for_this = 0
        for token in tokens:                    # para cada palbara dentro de nuestra oracion
            if token in embeddingsDictionary:   # si la palabra se encuentra en nuestro diccionario - entonces
                sentenceEmbedding += embeddingsDictionary[token] #suma acumulada de los embeddings por palabra para nuestro review
                #count_for_this +=1
        embeddedSentences.append(sentenceEmbedding)# salvar el embedding del review
    return embeddedSentences


trainEmb  = featureEmbedding(train_x,diccEmb)
valEmb    = featureEmbedding(val_x,diccEmb)
testEmb   = featureEmbedding(test_x,diccEmb)

In [95]:
print("Train-Emb:", len(trainEmb))
print("Val-Emb:", len(valEmb))
print("Test-Emb:", len(testEmb))

Train-Emb: 2100
Val-Emb: 450
Test-Emb: 450


In [ ]:
def zipSentenceEmbeddingWithLabel(embeddings, label):
  for x,c in zip(Xclean, Y):
    if c==1:
      pt.extend(x)   # comentarios positivos tienen clase 1
    else:
      nt.extend(x)

In [ ]:
# Veamos las dimensiones de cada conjunto embebido:

print("Train-Emb:", trainEmb.shape)
print("Val-Emb:", valEmb.shape)
print("Test-Emb:", testEmb.shape)

#**Pregunta - 8:**



Utiliza los modelos de regresión logística y bosque aleatorio (random forest) y encuentra sus desempeños.

Compara los resultados con los de la semana anterior.

In [97]:
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report

In [99]:
# REGRESIÓN LOGÍSTICA:

# ******* Inlcuye a continuación todas las líneas de código y celdas que requieras: ***********

logisticClassifier = LogisticRegression(random_state=345)
logisticClassifier.fit(trainEmb, y_train)
print("Accuracy: ", logisticClassifier.score(testEmb, y_test))

predsLogisticR = logisticClassifier.predict(valEmb)
print(classification_report(y_val, predsLogisticR))

# *********** Aquí termina la sección de agregar código *************


Accuracy:  0.8177777777777778
              precision    recall  f1-score   support

           0       0.82      0.82      0.82       239
           1       0.80      0.80      0.80       211

    accuracy                           0.81       450
   macro avg       0.81      0.81      0.81       450
weighted avg       0.81      0.81      0.81       450



In [100]:
# BOSQUE ALEATORIO (Random Forest):

# ******* Inlcuye a continuación todas las líneas de código y celdas que requieras: ***********

randForestClassifier = RandomForestClassifier(random_state=345)
randForestClassifier.fit(trainEmb, y_train)
print("Accuracy: ", randForestClassifier.score(testEmb, y_test))

predsRandomForest = randForestClassifier.predict(valEmb)
print(classification_report(y_val, predsRandomForest))


# *********** Aquí termina la sección de agregar código *************

Accuracy:  0.8
              precision    recall  f1-score   support

           0       0.79      0.79      0.79       239
           1       0.76      0.76      0.76       211

    accuracy                           0.78       450
   macro avg       0.77      0.77      0.77       450
weighted avg       0.78      0.78      0.78       450



#**Pregunta - 9:**



Reporte del mejor modelo.


In [ ]:
# ******* Inlcuye a continuación todas las líneas de código y celdas que requieras: ***********


None


# *********** Aquí termina la sección de agregar código *************

#**Pregunta - 10:**



Incluye tus comentarios finales de la actividad.

### ++++++++ Inicia la sección de agregar texto: +++++++++++

None

### ++++++++ Termina la sección de agregar texto: +++++++++++

##**Fin de la Actividad de vectores Embebidos - FastText**